# Aldabra - DroneMD (Metadata) Notebook

### Common variables:

In [1]:
# Script folder
dronemdt_folder = '/home/sylvain/DroneMDT'
# Session / Flight data input
input = '/home/sylvain/HDD5To/DATA/ALDABRA'
# Output geoflow config (json and csv entities)
output = '/home/sylvain/HDD5To/DATA/ALDABRA'
# Geoflow folder where .env is stored and jobs will be available
geoflow_folder = '/home/sylvain/geoflow-g2oi'
# Geoserver configuration
WS = 'MONACOEXPLORATIONS'
DS = 'aldabra'
# Zenodo setup
sandbox = False
# Move to dronemdt_folder
import os
os.chdir(dronemdt_folder)

## Part 1a: Check images validity

In [11]:
# DATA have to be copied from Drone internal storage or sdcard DCIM folder using suh naming convention:
# YYYYMMDD_COUNTRYCODE-optionalplace_device_session-number
# ├── DCIM :  folder to store videos and photos depending on the media collected
#
# Check validity of images copied from Drone to disk
# rclone copy cloudIRD:/G2OI/Missions/Aldabra /media/HDD5To/DATA/ALDABRA/

In [3]:
from check_images import *
img_list = im_list(input)
for i in range(len(img_list)):
    # print(i, img_list[i])
    imgv = Image.open(img_list[i])
    # imgv = check_image_with_pil(img_list[i])
    print(img_list[i], imgv)

/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21/METADATA/tb/DJI_0283_tbb51777e7.jpg <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=400x267 at 0x7F6B35855270>
/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21/METADATA/tb/DJI_0218_tb7322e2e1.jpg <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=400x267 at 0x7F6B2463A470>
/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21/METADATA/tb/DJI_0215_tb874ae46c.jpg <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=400x267 at 0x7F6B2463AE30>
/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21/METADATA/tb/DJI_0273_tb0085e1cc.jpg <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=400x267 at 0x7F6B2463A470>
/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21/METADATA/tb/DJI_0243_tb17d0986e.jpg <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=400x267 at 0x7F6B2463AE30>
/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-

## Part 1b: Generate report

In [4]:
## Using subprocess:
# import subprocess
# subprocess.check_output(["Rscript", "./generate_drone_metadata.R", input])
# from rpy2.robjects.packages import importr


## Part 2: Generate metadata

In [2]:
# Import packages and modules
import os
import shutil
import pandas as pd
import geopandas as gpd
import datetime
# from IPython.display import display
import argparse
import json
import pycountry
os.chdir(dronemdt_folder)
from meteo_helper import meteo
from read_metadata import *
from exif_helper import *
from enriched_func import *
from zenodo_helper import *
from zip_helper import *
from geoflow_helper import *
from raster_helper import *
from process_webodm import *
from settings import *

In [3]:
### Filter foder name
folder_name = filter_folder_name(input, 'UAV')
folder_name

['20221023_SYC-aldabra-arm06_UAV-02_21',
 '20221025_SYC-aldabra-arm01_UAV-02_33',
 '20221022_SYC-aldabra-passe-dubois_UAV-02_14',
 '20221024_SYC-aldabra-passe-dubois-MSP_UAV-02_27',
 '20221020_SYC-aldabra-arm01_UAV-02_3',
 '20221020_SYC-aldabra-arm01_UAV-02_6',
 '20221024_SYC-aldabra-passe-dubois-40m_UAV-02_26',
 '20221020_SYC-aldabra-arm01_UAV-02_4',
 '20221023_SYC-aldabra-arm06_UAV-02_20',
 '20221020_SYC-aldabra-arm01_UAV-02_5',
 '20221021_SYC-aldabra-arm01_UAV-02_8',
 '20221022_SYC-aldabra-arm06_UAV-02_16',
 '20221024_SYC-aldabra-gigi_UAV-02_30',
 '20221019_SYC-aldabra-arm01_UAV-02_1',
 '20221023_SYC-aldabra-arm06_UAV-02_19',
 '20221024_SYC-aldabra-passe-dubois-40m_UAV-02_25',
 '20221022_SYC-aldabra-arm06_UAV-02_15',
 '20221021_SYC-aldabra-arm01_UAV-02_10',
 '20221022_SYC-aldabra-passe-dubois_UAV-02_12',
 '20221022_SYC-aldabra-passe-dubois_UAV-02_11',
 '20221020_SYC-aldabra-arm01_UAV-02_1',
 '20221021_SYC-aldabra-arm01_UAV-02_9',
 '20221024_SYC-aldabra-passe-arm01_UAV-02_28',
 '2022

In [4]:
### Put data in basic panda dataframe
df = {}
df = basic_geoflow_df(folder_name)
df.head()

Identifier  \
0             20221023_SYC-aldabra-arm06_UAV-02_21   
1             20221025_SYC-aldabra-arm01_UAV-02_33   
2      20221022_SYC-aldabra-passe-dubois_UAV-02_14   
3  20221024_SYC-aldabra-passe-dubois-MSP_UAV-02_27   
4              20221020_SYC-aldabra-arm01_UAV-02_3   

                                                   Title  \
0             title:20221023 syc aldabra arm06 uav 02 21   
1             title:20221025 syc aldabra arm01 uav 02 33   
2      title:20221022 syc aldabra passe dubois uav 02 14   
3  title:20221024 syc aldabra passe dubois msp uav 02 27   
4              title:20221020 syc aldabra arm01 uav 02 3   

                                  Description       Subject       Creator  \
0  abstract:'No           \n\ndescription\n!'  project:None  creator:None   
1  abstract:'No           \n\ndescription\n!'  project:None  creator:None   
2  abstract:'No           \n\ndescription\n!'  project:None  creator:None   
3  abstract:'No           \n\ndescription\n!'  project:None  creator:None   
4  abstract:'No           \n\ndescription\n!'  project:None  creator:None   

                                          Date     Type Language  \
0  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
1  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
2  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
3  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
4  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   

  SpatialCoverage   TemporalCoverage Relation  \
0                  SYC-aldabra-arm06     None   
1                  SYC-aldabra-arm06     None   
2                  SYC-aldabra-arm06     None   
3                  SYC-aldabra-arm06     None   
4                  SYC-aldabra-arm06     None   

                                                                                                     Rights  \
0  useLimitation:Utilisation libre sous réserve de mentionner la source (a minima le nom du producteur) ...   
1  useLimitation:Utilisation libre sous réserve de mentionner la source (a minima le nom du producteur) ...   
2  useLimitation:Utilisation libre sous réserve de mentionner la source (a minima le nom du producteur) ...   
3  useLimitation:Utilisation libre sous réserve de mentionner la source (a minima le nom du producteur) ...   
4  useLimitation:Utilisation libre sous réserve de mentionner la source (a minima le nom du producteur) ...   

  Provenance              Format  Data  
0       None  resource:image/jpg  None  
1       None  resource:image/jpg  None  
2       None  resource:image/jpg  None  
3       None  resource:image/jpg  None  
4       None  resource:image/jpg  None

In [5]:
### Define Metadata file
md_file = 'metadata.txt'
### Parse global metadata
mdt_df_glob = global_mdt(input, md_file)
#### Enrich metadata
enrich_drone_mdt(input, df, md_file, mdt_df_glob)

INFO: Global `metadata.txt` found !
WARN: No metadata.txt in /home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21/METADATA to parse
INFO: GPS Folder found
Format id to obtain date, country name, optionnal place, and platform
####################
### 2. Enrich Title
 ####################
INFO: Using glocal title
Aerial images collected by UAV {platform}, {place}, {country} - {date}
format field
####################
### 8. Enrich Language
 ####################
INFO: Using glocal language
####################
### 4. Enrich Subject
 ####################
INFO: Using glocal theme
INFO: Using glocal project
####################
### 5. Enrich Creator
 ####################
INFO: Using glocal author
INFO: Using glocal publisher
INFO: Using glocal owner
INFO: Using glocal pointOfContact
INFO: Using glocal processor
####################
### 11. Enrich Relation
 ####################
INFO: Using glocal thumbnail
INFO: Using glocal http
####################
### Reading DCIM folder
 

/home/sylvain/DroneMDT/enriched_func.py:14: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  enriched = df_global.iloc[0][keyword][0]


/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21
Generate image with a set of images
Nb images:  84
preview 8 x  8
####################
### 10. Enrich TemporalCoverage
 ####################
####################
### 00. Prepare Provenance (13) and Description (3) 
 ####################
/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21/DCIM/DJI_0228.JPG
####################
Fetching open-meteo
 ####################
Location: -9.378722400000001, 46.2113668
Begin: 2022-10-23 10-55-50 - End: 2022-10-23 11-06-22
Model: best_match


  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  2026    0  2026    0     0   9396      0 --:--:-- --:--:-- --:--:--  9423


Convert Dataframe to UTM
Index(['FileName', 'GPSLatitude', 'GPSLongitude', 'GPSAltitude',
       'FlightRollDegree', 'FlightPitchDegree', 'FlightYawDegree',
       'GimbalRollDegree', 'GimbalPitchDegree', 'GimbalYawDegree',
       'ImageWidth', 'ImageLength', 'BitsPerSample', 'ImageDescription',
       'Make', 'Model', 'Orientation', 'SamplesPerPixel', 'XResolution',
       'YResolution', 'ResolutionUnit', 'Software', 'DateTime',
       'YCbCrPositioning', 'ExifOffset', 'GPSVersionID', 'ThumbnailImageWidth',
       'ThumbnailImageLength', 'ThumbnailCompression', 'ThumbnailXResolution',
       'ThumbnailYResolution', 'ThumbnailResolutionUnit',
       'ThumbnailJPEGInterchangeFormat',
       'ThumbnailJPEGInterchangeFormatLength', 'ExposureTime', 'FNumber',
       'ExposureProgram', 'ISOSpeedRatings', 'ExifVersion', 'DateTimeOriginal',
       'DateTimeDigitized', 'ComponentsConfiguration', 'ExposureBiasValue',
       'MaxApertureValue', 'MeteringMode', 'LightSource', 'Flash',
       'Foc

...

Convert Dataframe to UTM
Index(['FileName', 'GPSLatitude', 'GPSLongitude', 'GPSAltitude',
       'FlightRollDegree', 'FlightPitchDegree', 'FlightYawDegree',
       'GimbalRollDegree', 'GimbalPitchDegree', 'GimbalYawDegree',
       'ImageWidth', 'ImageLength', 'BitsPerSample', 'ImageDescription',
       'Make', 'Model', 'Orientation', 'SamplesPerPixel', 'XResolution',
       'YResolution', 'ResolutionUnit', 'Software', 'DateTime',
       'YCbCrPositioning', 'ExifOffset', 'GPSVersionID', 'ThumbnailImageWidth',
       'ThumbnailImageLength', 'ThumbnailCompression', 'ThumbnailXResolution',
       'ThumbnailYResolution', 'ThumbnailResolutionUnit',
       'ThumbnailJPEGInterchangeFormat',
       'ThumbnailJPEGInterchangeFormatLength', 'ExposureTime', 'FNumber',
       'ExposureProgram', 'ISOSpeedRatings', 'ExifVersion', 'DateTimeOriginal',
       'DateTimeDigitized', 'ComponentsConfiguration', 'ExposureBiasValue',
       'MaxApertureValue', 'MeteringMode', 'LightSource', 'Flash',
       'Foc

/home/sylvain/DroneMDT/enriched_func.py:14: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  enriched = df_global.iloc[0][keyword][0]


/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_17
Generate image with a set of images
Nb images:  277
preview 8 x  8
####################
### 10. Enrich TemporalCoverage
 ####################
####################
### 00. Prepare Provenance (13) and Description (3) 
 ####################
/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_17/DCIM/DJI_0159.JPG
####################
Fetching open-meteo
 ####################
Location: -4.6918528, 23.1068722
Begin: 2022-10-23 09-11-33 - End: 2022-10-23 09-27-32
Model: best_match


  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  1973    0  1973    0     0   9184      0 --:--:-- --:--:-- --:--:--  9219


Convert Dataframe to UTM
Index(['FileName', 'GPSLatitude', 'GPSLongitude', 'GPSAltitude',
       'FlightRollDegree', 'FlightPitchDegree', 'FlightYawDegree',
       'GimbalRollDegree', 'GimbalPitchDegree', 'GimbalYawDegree',
       'ImageWidth', 'ImageLength', 'BitsPerSample', 'ImageDescription',
       'Make', 'Model', 'Orientation', 'SamplesPerPixel', 'XResolution',
       'YResolution', 'ResolutionUnit', 'Software', 'DateTime',
       'YCbCrPositioning', 'ExifOffset', 'GPSVersionID', 'ThumbnailImageWidth',
       'ThumbnailImageLength', 'ThumbnailCompression', 'ThumbnailXResolution',
       'ThumbnailYResolution', 'ThumbnailResolutionUnit',
       'ThumbnailJPEGInterchangeFormat',
       'ThumbnailJPEGInterchangeFormatLength', 'ExposureTime', 'FNumber',
       'ExposureProgram', 'ISOSpeedRatings', 'ExifVersion', 'DateTimeOriginal',
       'DateTimeDigitized', 'ComponentsConfiguration', 'ExposureBiasValue',
       'MaxApertureValue', 'MeteringMode', 'LightSource', 'Flash',
       'Foc

In [6]:
# Set prefix for generated json and csv entities
out_prefix = datetime.datetime.now().strftime('%Y%m%d-%H%M%S')
out_prefix

'20240624-174615'

In [7]:
# Visualize output
df.head()

Identifier  \
0             20221023_SYC-aldabra-arm06_UAV-02_21   
1             20221025_SYC-aldabra-arm01_UAV-02_33   
2      20221022_SYC-aldabra-passe-dubois_UAV-02_14   
3  20221024_SYC-aldabra-passe-dubois-MSP_UAV-02_27   
4              20221020_SYC-aldabra-arm01_UAV-02_3   

                                                                                               Title  \
0             title:Aerial images collected by UAV UAV, Aldabra arm06, Seychelles - 20221023 - 02_21   
1             title:Aerial images collected by UAV UAV, Aldabra arm01, Seychelles - 20221025 - 02_33   
2      title:Aerial images collected by UAV UAV, Aldabra passe dubois, Seychelles - 20221022 - 02_14   
3  title:Aerial images collected by UAV UAV, Aldabra passe dubois msp, Seychelles - 20221024 - 02_27   
4              title:Aerial images collected by UAV UAV, Aldabra arm01, Seychelles - 20221020 - 02_3   

                                                                                                Description  \
0  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra arm06, Seychelles, on 2...   
1  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra arm01, Seychelles, on 2...   
2  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra passe dubois, Seychelle...   
3  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra passe dubois msp, Seych...   
4  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra arm01, Seychelles, on 2...   

                                                                                                    Subject  \
0  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   
1  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   
2  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   
3  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   
4  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   

                                                                                                    Creator  \
0  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   
1  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   
2  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   
3  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   
4  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   

                                          Date     Type Language  \
0  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
1  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
2  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
3  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
4  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   

  SpatialCoverage                           TemporalCoverage  \
0                  2022-10-23 10-55-50 - 2022-10-23 11-06-22   
1                  2022-10-25 12-14-07 - 2022-10-25 12-25-14   
2                  2022-10-22 09-39-50 - 2022-10-22 09-53-52   
3                  2022-10-24 10-40-53 - 2022-10-24 10-52-48   
4                  2022-10-20 10-13-31 - 2022-10-20 10-27-28   

                                                                                                   Relation  \
0  thumbnail:G2OI@https://raw.githubusercontent.com/IRDG2OI/.github/main/profile/logo_g2oi_final_1280px_...   
1  thumbnail:G2OI@https://raw.githubusercontent.com/IRDG2OI/.github/main/

In [8]:
# Visualize Description
print(df.iloc[0]['Description'])

abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra arm06, Seychelles, on 20221023
<br /> 
<br />Underwater or aerial images collected by scientists or citizens can have a wide variety of uses for science, ecosystems management, or conservation. These images can be annotated and shared to train IA models which can in turn predict the objects on such images. We provide a set of tools (hardware and software) to collect marine data, predict species or habitat, and provide maps.
<br />
<br /><b>The depot consists of the following elements:</b>
<br />- 00_: Image preview panel
<br />- DCIM.zip: RAW images from UAV
<br />- GPS.zip: GIS file (Geopackage) containing the overflight area as well as the geolocation of the images accompanied by their thumbnails in the base64 attribute table.
<br />- METADATA.zip: Exif metadata in CSV format, OGC metadata in ISO19115 / 39 XML format, flight reports with thumbnails of drone images (tb folder) and flight statistics (html or 

In [12]:
##############
#### ISO 19115 config
##############
## Export to csv
df.to_csv(os.path.join(output, out_prefix + "_iso19115-metadata.csv"), quoting=1, quotechar='"', index=False)
## Generate json
iso19115config = {'profile': {'id': 'iso19115', 
                              'name': 'iso19115', 
                              'project': 'Generate iso19115 with Geoflow', 
                              'organization': 'IRD', 
                              'environment': {'file': '.env', 
                                              'hide_env_vars': ['MOTDEPASSE']}, 
                              'logos': ['https://en.ird.fr/sites/ird_fr/files/2019-08/logo_IRD_2016_BLOC_UK_COUL.png'], 
                              'mode': 'entity'}, 
                  'metadata': {'entities': 
                               [{'handler': 'csv', 
                                 'source': os.path.join(output, out_prefix) + "_iso19115-metadata.csv"}], 
                               'contacts': 
                               [{'handler': 'csv', 
                                 'source': 'https://raw.githubusercontent.com/IRDG2OI/geoflow-g2oi/main/Action%201.3/METADATA_AND_CONFIGS/geoflow_g2oi_contacts.csv'}]}, 
                  'software': [], 
                  'actions': 
                  [{'id': 'geometa-create-iso-19115',
                    'options' : 
                    {"logo": True}, 
                    "run": True}]}

# Export json to file
with open(os.path.join(output, out_prefix + '_iso19115-config.json'), 'w') as f:
    json.dump(iso19115config, f, indent=4)

In [18]:
# Optional : could start from here => reload dataframe from csv
df = {}
df = pd.read_csv(os.path.join(output, out_prefix + "_iso19115-metadata.csv"))

In [13]:
### Execute geoflow
xml19115 = run_geoflow(os.path.join(output, out_prefix + '_iso19115-config.json'), geoflow_folder)
os.chdir(dronemdt_folder)

R[write to console]: Rows: 152 Columns: 14

R[write to console]: ── Column specification ────────────────────────────────────────────────────────
Delimiter: ","
chr (14): Identifier, Email, OrganizationName, PositionName, LastName, First...

R[write to console]: 
ℹ Use `spec()` to retrieve the full column specification for this data.
ℹ Specify the column types or set `show_col_types = FALSE` to quiet this message.

R[write to console]: Rows: 33 Columns: 15

R[write to console]: ── Column specification ────────────────────────────────────────────────────────
Delimiter: ","
chr (15): Identifier, Title, Description, Subject, Creator, Date, Type, Lang...

R[write to console]: 
ℹ Use `spec()` to retrieve the full column specification for this data.
ℹ Specify the column types or set `show_col_types = FALSE` to quiet this message.

R[write to console]: Loading required package: geometa

R[write to console]: Loading required package: ows4R



In [14]:
# Geoflow job log folder
print(xml19115[0])

/home/sylvain/geoflow-g2oi/jobs/20240624184051


In [15]:
## Copy generated ISO19115 to original metadata folder
for id in range(len(df)):
    jobs19115 = xml19115[0] + '/entities/' + df.iloc[id]['Identifier'] + '/metadata/'
    fname19115 = df.iloc[id]['Identifier'] + '_ISO-19115.xml'
    if fname19115 in os.listdir(jobs19115):
        shutil.copyfile(jobs19115+fname19115, 
                        input + "/" + df.iloc[id]['Identifier'] + '/METADATA/' + fname19115)

## Part 3. Upload RAW data to Zenodo

### ZIP all folders

In [20]:
### Zip all folders
zip_each_folder(input, df)
### Reference Zip's in Dataframe
for zip in range(len(df)):
    source = []
    sess_path = os.path.join(input, df.iloc[zip]['Identifier'])
    source = os.listdir(sess_path)
    if len(source) < 1:
        pass
    else:
        source_file = []
        for file in range(len(source)):
            if "PROCESSED_DATA.zip" in source:
                pass
            else:
                if os.path.isfile(os.path.join(sess_path, source[file])):
                    if len(source) < 2:
                        df.iloc[zip, df.columns.get_loc('Data')] = "source:" + source[file] + "@" + sess_path + "/" + source[file] + "_\n" + "sourceType:other_\nsourceZip:false"
                        source_file = source[file]
                    else:
                        source_file.append(source[file])
                        # df.iloc[zip, df.columns.get_loc('Data')] = "source:" + source[file] + "@" + sess_path + source[file] + "_\n" + "sourceType:other_\nsourceZip:false"
        if ".zip" in  df.iloc[zip, df.columns.get_loc('Data')]:
            pass
        else:
            df.iloc[zip, df.columns.get_loc('Data')] = "source:"
            for i in range(len(source_file)):
                df.iloc[zip, df.columns.get_loc('Data')] =  str(df.iloc[zip, df.columns.get_loc('Data')]) + source_file[i] + "@" + sess_path + "/" + source_file[i] + ","
    
    if "," in str(df.iloc[zip, df.columns.get_loc('Data')])[-1]:
        df.iloc[zip, df.columns.get_loc('Data')] = str(df.iloc[zip, df.columns.get_loc('Data')])[:-1] + "_\n" + "sourceType:other_\nupload:true"


INFO: Ziping 20221023_SYC-aldabra-arm06_UAV-02_21
    INFO: 00_sample_rawdata_overview.png is not a folder
INFO: Ziping 20221025_SYC-aldabra-arm01_UAV-02_33
    INFO: 00_sample_rawdata_overview.png is not a folder
INFO: Ziping 20221022_SYC-aldabra-passe-dubois_UAV-02_14
    INFO: 00_sample_rawdata_overview.png is not a folder
INFO: Ziping 20221024_SYC-aldabra-passe-dubois-MSP_UAV-02_27
    INFO: 00_sample_rawdata_overview.png is not a folder
INFO: Ziping 20221020_SYC-aldabra-arm01_UAV-02_3
    INFO: 00_sample_rawdata_overview.png is not a folder
INFO: Ziping 20221020_SYC-aldabra-arm01_UAV-02_6
    INFO: 00_sample_rawdata_overview.png is not a folder
INFO: Ziping 20221024_SYC-aldabra-passe-dubois-40m_UAV-02_26
    INFO: 00_sample_rawdata_overview.png is not a folder
INFO: Ziping 20221020_SYC-aldabra-arm01_UAV-02_4
    INFO: 00_sample_rawdata_overview.png is not a folder
INFO: Ziping 20221023_SYC-aldabra-arm06_UAV-02_20
    INFO: 00_sample_rawdata_overview.png is not a folder
INFO: Zipin

### Generate config files for geoflow or re-use dataframe later

In [22]:
### Export raw data df to csv
fname = out_prefix + '_zenodo-rawdata'
df.to_csv(os.path.join(output, fname + ".csv"), quoting=1, quotechar='"', index=False)

### Configure and export Zenodo json
# SANDBOX
# zen_json = zenodo_json(fname, 'sandbox', output, out_prefix)
# PRODUCTION
zen_json = zenodo_json(fname, 'no_sandbox', output, out_prefix)
with open(os.path.join(output, out_prefix + '_rawfiles-config.json'), 'w') as f:
    json.dump(zen_json, f, indent=4)

### Execute Geoflow to upload to Zenodo
/!\ DISABLED SINCE FRIDAY 2023 10 13 /!\
/!\ Zenodo upgrade /!\

In [23]:
# ### Execute geoflow :: upload to geoflow
# # upload_raw_to_zenodo = 
# config_raw = os.path.join(output, out_prefix + '_rawfiles-config.json')
# # run_geoflow(config_raw, geoflow_folder)
# os.chdir(geoflow_folder)
# # subprocess.run(["R", "-e", "geoflow::initWorkflow('{}')".format(config_raw)], capture_output=False)
# subprocess.call(["R", "-e", "geoflow::executeWorkflow('{}')".format(config_raw)],
#                 stdout=subprocess.DEVNULL, stderr=subprocess.STDOUT,)
# os.chdir(dronemdt_folder)

### Upload to Zenodo with Python

In [62]:
%load_ext autoreload
%autoreload 2

# del(zenul)
from zenodo_helper import *
import hashlib
# help(zenul)
# data_zip

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [31]:
### Upload to Zenodo
print("#### Upload zip files to Zenodo")
base_url = "https://zenodo.org/api/"
for zipul in range(len(df)):
    # print("Dataset:", zipul, "/" ,len(df))
    print('\nDataset:', zipul+1, "/" ,len(df), "\n    ",df.iloc[zipul]['Identifier'])
    zenodo_baseurl = base_url

    #### Extract source from Data in dataframe
    data_zip = df.iloc[zipul]['Data'].split('source:')[1].split('_\n')[0]
    if "," in data_zip:
        data_ziptemp = data_zip.split(',')
        data_zip = []
        for dt in range(len(data_ziptemp)):
            data_zip.append(data_ziptemp[dt].split('@')[0])
    else:
        data_zip = data_zip.split('@')[0]
    # data_zip = source_file
    print(data_zip)

    ### Put Metadata or verify if doi exists (Metadata not updated if doi exists)
    if 'doi:' in df.iloc[zipul]['Identifier']:
        doi_raw = df.iloc[zipul]['Identifier'].split('_\ndoi:')[1].split('\n')[0].split('.')[-1]
        print("DOI already present: ",doi_raw)
        getrecid = zenlist_single(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
        zenval = zenvar(getrecid)
    else:
        print("Initialize deposit")
        r = check_token(zenodo_baseurl, ACCESS_TOKEN)
        zenval = zenvar(r)
        print("prereserved doi:"+zenval[1])
        print("Write DOI to dataframe")
        dfzen = df
        if 'id:' in dfzen.iloc[zipul]['Identifier']:
            pass
        else:
            dfzen.iloc[zipul, dfzen.columns.get_loc('Identifier')] = "id:" + dfzen.iloc[zipul]['Identifier'] + "_\ndoi:" + zenval[1]
            dfzen.iloc[zipul, dfzen.columns.get_loc("Provenance")] = dfzen.iloc[zipul]["Provenance"] + "_\nprocess:Raw dataset uploaded to " + base_url.split('api')[0] + "record/" + str(zenval[2])
            
        print("Enrich upload with metadata")
        zen_metadata = zenmdt(zenodo_baseurl, ACCESS_TOKEN, zenval[2], df, zipul)
        if zen_metadata.status_code > 400:
            print("error in metadata, please check there is no double keywords: \n" + zen_metadata.text)
            break
        
    # print(zen_metadata.text)       
    print("upload data")
    print("Trying upload number: 1")

    for file in data_zip:
        ul_count = 1
        ### Control Filename
        # while file not in zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2])).text:
        ### Control md5 checksum:
        ful = os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1], file)
        print(ful)
        with open(ful, "rb") as file_to_check:
            # Open,close, read file and calculate MD5 on its contents 
            # read contents of the file
            ## Python 3.10
            fh = file_to_check.read() 
            # pipe contents of the file through
            digest = hashlib.md5(fh)
            ## End Python 3.10
            # digest = hashlib.file_digest(file_to_check, "md5") ### Python 3.11 only
        print("    md5:", digest.hexdigest())
        while digest.hexdigest() not in zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2])).text:
            #Reset connection every 15 tries
            if ul_count == 15:
                getrecid = zenlist_single(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
                zenval = zenvar(getrecid)
            
            file_on_server = zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2]))
            ### Clean wrong checksum
            if file in file_on_server.text:
                print("    clean wrong files")
                for fs in range(len(file_on_server.json())):
                    if file == file_on_server.json()[fs]['filename']:
                        # print("    sleep 5: computing checksum on server")
                        # time.sleep(15)
                        print("    checksum on server", file_on_server.json()[fs]['checksum'])
                        furl = file_on_server.json()[fs]["links"]["self"]
                        file_to_remove = zen_del_file(furl, ACCESS_TOKEN)
                        
            file_list = [file]            
            zen_upload = zenul(zenval[0], ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), file_list)
            print("        ", zen_upload.text)
            if zen_upload.status_code == 404:
                print("Version doesn't exists ! Please check your record_id")
                break
            else:
                print("    Retry number: " + str(ul_count))                
                ul_count += 1
                if zen_upload.status_code == 403:
                    print("        Friday 13th 2023 nightmare => permission denied!")
                    time.sleep(5)      
            
    # zen_upload = zenul(zenval[0], ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), data_zip)
    # # for file in data_zip:
    # #     print("Uploading: ", file)
    # #     print("curl", "--upload-file", os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1], file), zenval[0] + "/" + file + "?" + "k3LQP8uj4HtpRbjMMXMIUBeRJr0UFELUwjyXWIakTHh0xP9p5PhZ7bzCqRN1")
    # #     subprocess.check_output(["curl", "--upload-file", 
    # #                              os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1], file),
    # #                              zenval[0] + "/" + file + "?" + "k3LQP8uj4HtpRbjMMXMIUBeRJr0UFELUwjyXWIakTHh0xP9p5PhZ7bzCqRN1"
    # #                                           ])
    # if zen_upload.status_code != 201:
    #     for file in data_zip:
    #         file_list = [file]
    #         zen_upload = zenul(zenval[0], ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), file_list)
    #         # zen_upload = zenul(zenvar(newv), ACCESS_TOKEN, os.getcwd(), test_list)
    #         # zen_upload = zenul2(zenodo_baseurl, str(zenval[-1]), ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), data_zip)
    #         print("Upload status OK? " + str(zen_upload.ok))
    #         print("Control files: first pass")
    #         ul_count = 1
    #         while zen_upload.status_code != 201:
    #             if zen_upload.status_code == 404:
    #                 print("Version doesn't exists ! Please check your record_id")
    #                 break
    #             else:
    #                 ul_count += 1
    #                 print("Retry number: " + str(ul_count))
    #                 zen_upload = zenul(zenval[0], ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), file_list)
    #                 if zen_upload.status_code == 403:
    #                     print("        Friday 13th 2023 nightmare => permission denied!")
    #                     time.sleep(5)
                    
            # zen_metadata = zenmdt(zenodo_baseurl, ACCESS_TOKEN, zenval[2], df, zipul)
            ## Too agressive                
            # print("Control files: second pass")
            # if zen_upload.status_code == 201:
            #     # files_ul = zenfiles(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2]))
            #     # while len(zenfiles(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2])).json()) != len(data_zip):
            #     while file not in zenfiles(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2])).json():
            #         if zen_upload.status_code == 404:
            #             print("Version doesn't exists ! Please check your record_id")
            #             break
            #         else:
            #             ul_count += 1
            #             print("Retry number: " + str(ul_count))
            #             zen_upload = zenul(zenval[0], ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), file_list)
            #             # files_ul = zenfiles(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2]))       
            

    # ### Publish to Zenodo
    # print("Publish record")
    # zenpublish(zenodo_baseurl, ACCESS_TOKEN, zenval[2])

#### Upload zip files to Zenodo

Dataset: 1 / 33 
     id:20221023_SYC-aldabra-arm06_UAV-02_21_
doi:10.5281/zenodo.12522502
['GPS.zip', '00_sample_rawdata_overview.png', 'DCIM.zip', 'METADATA.zip']
DOI already present:  12522502
upload data
Trying upload number: 1
/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21/GPS.zip
    md5: 0119a5eb2e807cce04c8a7be6b1dbff5
/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21/00_sample_rawdata_overview.png
    md5: 7e75c8dc5f7fc60cc8a9d0de51a26eef
/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21/DCIM.zip
    md5: cbde29dcc0d27e35adb42e6351969874
/home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21/METADATA.zip
    md5: f31ece25a5211b4ff54e5f7224ea55bf
    Sleep 5 seconds before new upload
upload: METADATA.zip
         {"created": "2024-06-25T07:01:13.616519+00:00", "updated": "2024-06-25T07:01:13.757836+00:00", "version_id": "2c9a6af8-9e9c-44e0-87a9-a9e6b2f358c6", "key"

In [32]:
### Control on last upload
print("Uploaded files available for record:", zenval[2])
a = zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2]))
for i in range(len(a.json())):
    print("  |__" ,a.json()[i]['filename'])

Uploaded files available for record: 12522735
  |__ DCIM.zip
  |__ 00_sample_rawdata_overview.png
  |__ GPS.zip
  |__ METADATA.zip


In [28]:
### Check DOI's

for doi in range(len(df)):
    print(df.iloc[doi]["Identifier"])

id:20221023_SYC-aldabra-arm06_UAV-02_21_
doi:10.5281/zenodo.12522502
id:20221025_SYC-aldabra-arm01_UAV-02_33_
doi:10.5281/zenodo.12522508
id:20221022_SYC-aldabra-passe-dubois_UAV-02_14_
doi:10.5281/zenodo.12522515
id:20221024_SYC-aldabra-passe-dubois-MSP_UAV-02_27_
doi:10.5281/zenodo.12522527
id:20221020_SYC-aldabra-arm01_UAV-02_3_
doi:10.5281/zenodo.12522537
id:20221020_SYC-aldabra-arm01_UAV-02_6_
doi:10.5281/zenodo.12522543
id:20221024_SYC-aldabra-passe-dubois-40m_UAV-02_26_
doi:10.5281/zenodo.12522545
id:20221020_SYC-aldabra-arm01_UAV-02_4_
doi:10.5281/zenodo.12522547
id:20221023_SYC-aldabra-arm06_UAV-02_20_
doi:10.5281/zenodo.12522555
id:20221020_SYC-aldabra-arm01_UAV-02_5_
doi:10.5281/zenodo.12522559
id:20221021_SYC-aldabra-arm01_UAV-02_8_
doi:10.5281/zenodo.12522562
id:20221022_SYC-aldabra-arm06_UAV-02_16_
doi:10.5281/zenodo.12522575
id:20221024_SYC-aldabra-gigi_UAV-02_30_
doi:10.5281/zenodo.12522594
id:20221019_SYC-aldabra-arm01_UAV-02_1_
doi:10.5281/zenodo.12522600
id:20221023_

In [29]:
### Export Dataframe to csv
# ### Export Dataframe to csv
csv_published = out_prefix + "_zenodo-rawdata"
df.to_csv(os.path.join(output, csv_published + ".csv"), quoting=1, quotechar='"', index=False)
# ### Export geoflow config to json
if sandbox == True:
    zenodo_url = "https://sandbox.zenodo.org/api"
else:
    zenodo_url = "https://zenodo.org/api"
rawdata_config = {'profile': {'id': 'rawdata', 'name': 'rawdata', 'project': 'Publish rawdata with Geoflow', 'organization': 'IRD', 'environment': {'file': '.env', 'hide_env_vars': ['MOTDEPASSE']}, 'logos': ['https://en.ird.fr/sites/ird_fr/files/2019-08/logo_IRD_2016_BLOC_UK_COUL.png'], 'mode': 'entity'}, 'metadata': {'entities': [{'handler': 'csv', 'source': os.path.join(output, out_prefix) + "_zenodo-rawdata.csv"}], 'contacts': [{'handler': 'csv', 'source': 'https://drive.ird.fr/s/EYS3qccyB28PrA9/download/geoflow_g2oi_contacts.csv'}]}, 'software': [{"id": "my-zenodo","type": "output","software_type": "zenodo","parameters": {"url": zenodo_url,"token": "{{ ZENODO_TOKEN }}","logger": "DEBUG"},"properties": {"clean": {"run": False}}}], 'actions': [{"id": "zen4R-deposit-record","options": {"update_files": True,"communities": "uav","depositWithFiles": True,"publish": False,"update_metadata": True,"strategy": "newversion","deleteOldFiles": True},"run": True}]}
with open(os.path.join(output, out_prefix + '_zenodo-rawdata-config.json'), 'w') as f:
    json.dump(rawdata_config, f, indent=4)

### Update RAW Metadata 

In [37]:
# Reload Raw Dataframe
out_prefix = '20240624-174615'
df = {}
df = pd.read_csv(os.path.join(input, out_prefix + '_zenodo-rawdata.csv'))
df.head()

Identifier  \
0             id:20221023_SYC-aldabra-arm06_UAV-02_21_\ndoi:10.5281/zenodo.12522502   
1             id:20221025_SYC-aldabra-arm01_UAV-02_33_\ndoi:10.5281/zenodo.12522508   
2      id:20221022_SYC-aldabra-passe-dubois_UAV-02_14_\ndoi:10.5281/zenodo.12522515   
3  id:20221024_SYC-aldabra-passe-dubois-MSP_UAV-02_27_\ndoi:10.5281/zenodo.12522527   
4              id:20221020_SYC-aldabra-arm01_UAV-02_3_\ndoi:10.5281/zenodo.12522537   

                                                                                           Title  \
0             title:Aerial images collected by UAV, Aldabra arm06, Seychelles - 20221023 - 02_21   
1             title:Aerial images collected by UAV, Aldabra arm01, Seychelles - 20221025 - 02_33   
2      title:Aerial images collected by UAV, Aldabra passe dubois, Seychelles - 20221022 - 02_14   
3  title:Aerial images collected by UAV, Aldabra passe dubois msp, Seychelles - 20221024 - 02_27   
4              title:Aerial images collected by UAV, Aldabra arm01, Seychelles - 20221020 - 02_3   

                                                                                                Description  \
0  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra arm06, Seychelles, on 2...   
1  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra arm01, Seychelles, on 2...   
2  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra passe dubois, Seychelle...   
3  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra passe dubois msp, Seych...   
4  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra arm01, Seychelles, on 2...   

                                                                                                    Subject  \
0  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   
1  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   
2  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   
3  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   
4  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   

                                                                                                    Creator  \
0  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   
1  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   
2  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   
3  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   
4  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   

                                          Date     Type Language  \
0  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
1  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
2  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
3  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
4  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   

   SpatialCoverage                           TemporalCoverage  \
0              NaN  2022-10-23 10-55-50 - 2022-10-23 11-06-22   
1              NaN  2022-10-25 12-14-07 - 2022-10-25 12-25-14   
2              NaN  2022-10-22 09-39-50 - 2022-10-22 09-53-52   
3              NaN  2022-10-24 10-40-53 - 2022-10-24 10-52-48   
4              NaN  2022-10-20 10-13-31 - 2022-10-20 10-27-28   

                                                                                                   Relation  \
0  thumbnail:G2OI@https://raw.githubu

In [40]:
### Update Metadata
print("#### Update metadata")
base_url = "https://zenodo.org/api/"
for zipul in range(len(df)):
    print('\nDataset:', zipul+1, "/" ,len(df), "\n    ",df.iloc[zipul]['Identifier'])
    zenodo_baseurl = base_url 
    
    if 'doi:' in df.iloc[zipul]['Identifier']:
        doi_raw = df.iloc[zipul]['Identifier'].split('_\ndoi:')[1].split('_\n')[0].split('.')[-1]
        # print("\nDOI already present: ",doi_raw)
        # getrecid = zenlist_single(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
        # print(getrecid.text)
        
        # zenval = zenvar(getrecid)
        # print(zenval)
        # print("\nEnrich upload with metadata")
        zenedit(zenodo_baseurl, ACCESS_TOKEN, doi_raw)
        zen_metadata = zenmdt(zenodo_baseurl, ACCESS_TOKEN, doi_raw, df, zipul, contact_file="/home/sylvain/DroneMDT/geoflow_g2oi_contacts.csv")
        print(zen_metadata)

    ### Publish to Zenodo
    print("Publish record")
    published = zenpublish(zenodo_baseurl, ACCESS_TOKEN, doi_raw)
    print(published.text)
    print("#### END !")

#### Update metadata

Dataset: 1 / 33 
     id:20221023_SYC-aldabra-arm06_UAV-02_21_
doi:10.5281/zenodo.12522502
Using contact file
  Looking for julien.barde@ird.fr
    Look for email julien.barde@ird.fr in Contact file
      Add orcid
      Add First and Last Name
      Add Affiliation
  Looking for sylvain.bonhommeau@ifremer.fr
    Look for email sylvain.bonhommeau@ifremer.fr in Contact file
      Add orcid
      Add First and Last Name
      Add Affiliation
  Looking for victor.illien@ifremer.fr
    Look for email victor.illien@ifremer.fr in Contact file
      Add First and Last Name
      Add Affiliation
  Looking for matteo.contini@ifremer.fr
    Look for email matteo.contini@ifremer.fr in Contact file
      Add orcid
      Add First and Last Name
      Add Affiliation
  Looking for serge.bernard@lirmm.fr
    Look for email serge.bernard@lirmm.fr in Contact file
      Add First and Last Name
      Add Affiliation
  Looking for sylvain.poulain@ird.fr
    Look for email sylvain.pou

## Part 4. Download from ODM

In [56]:
# Take csv generated from python zenodo upload as updated dataframe
# Reload Raw Dataframe
out_prefix = '20240624-174615'
df = {}
df = pd.read_csv(os.path.join(input, out_prefix + '_zenodo-rawdata.csv'))
df.head()

Identifier  \
0             id:20221023_SYC-aldabra-arm06_UAV-02_21_\ndoi:10.5281/zenodo.12522502   
1             id:20221025_SYC-aldabra-arm01_UAV-02_33_\ndoi:10.5281/zenodo.12522508   
2      id:20221022_SYC-aldabra-passe-dubois_UAV-02_14_\ndoi:10.5281/zenodo.12522515   
3  id:20221024_SYC-aldabra-passe-dubois-MSP_UAV-02_27_\ndoi:10.5281/zenodo.12522527   
4              id:20221020_SYC-aldabra-arm01_UAV-02_3_\ndoi:10.5281/zenodo.12522537   

                                                                                           Title  \
0             title:Aerial images collected by UAV, Aldabra arm06, Seychelles - 20221023 - 02_21   
1             title:Aerial images collected by UAV, Aldabra arm01, Seychelles - 20221025 - 02_33   
2      title:Aerial images collected by UAV, Aldabra passe dubois, Seychelles - 20221022 - 02_14   
3  title:Aerial images collected by UAV, Aldabra passe dubois msp, Seychelles - 20221024 - 02_27   
4              title:Aerial images collected by UAV, Aldabra arm01, Seychelles - 20221020 - 02_3   

                                                                                                Description  \
0  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra arm06, Seychelles, on 2...   
1  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra arm01, Seychelles, on 2...   
2  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra passe dubois, Seychelle...   
3  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra passe dubois msp, Seych...   
4  abstract:"This dataset was collected by an Unmanned Aerial Vehicle in Aldabra arm01, Seychelles, on 2...   

                                                                                                    Subject  \
0  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   
1  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   
2  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   
3  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   
4  theme[General]: UAV, Artificial Intelligence, Bathymetry, Citizen Sciences, Computer Vision, Coral Re...   

                                                                                                    Creator  \
0  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   
1  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   
2  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   
3  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   
4  author:julien.barde@ird.fr,sylvain.bonhommeau@ifremer.fr,victor.illien@ifremer.fr,matteo.contini@ifre...   

                                          Date     Type Language  \
0  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
1  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
2  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
3  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   
4  publication:2024-06-24_\nedition:2024-06-24  dataset      eng   

   SpatialCoverage                           TemporalCoverage  \
0              NaN  2022-10-23 10-55-50 - 2022-10-23 11-06-22   
1              NaN  2022-10-25 12-14-07 - 2022-10-25 12-25-14   
2              NaN  2022-10-22 09-39-50 - 2022-10-22 09-53-52   
3              NaN  2022-10-24 10-40-53 - 2022-10-24 10-52-48   
4              NaN  2022-10-20 10-13-31 - 2022-10-20 10-27-28   

                                                                                                   Relation  \
0  thumbnail:G2OI@https://raw.githubu

In [42]:
### SEARCH AND DOWNLOAD FROM ODM
odm_projects = list_all_projects()
for projects in range(len(odm_projects)):
    for p in range(len(df)):
        if df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1] in odm_projects[projects]['name']:
            print(projects, odm_projects[projects]['id'], odm_projects[projects]['name'], odm_projects[projects]['tasks'])
            project_id = odm_projects[projects]['id']
            tasks =  odm_projects[projects]['tasks']
            res = requests.post(settings.SERVER + '/api/token-auth/', 
                            data={'username': settings.USERNAME,
                                'password': settings.PASSWORD}).json()
            if 'token' in res:
                print("Still logged-in!")
                token = res['token']
                for task in range(len(tasks)):
                    task_id = tasks[task]
                    print(task_id)
                    res = requests.get(settings.SERVER + "/api/projects/{}/tasks/{}/download/all.zip".format(project_id, task_id), 
                                    headers={'Authorization': 'JWT {}'.format(token)},
                                    stream=True)
                    # token = res['token']
                    sess_path = os.path.join(input, df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1])
                    ### Reading PROCESSED_DATA folder
                    ### Check and create PROCESSED_DATA Directory if it not exists
                    # process_dir=os.path.join(sess_path, 'PROCESSED_DATA')
                    # if os.path.exists(process_dir):
                    if os.path.exists(sess_path):
                        if 'PROCESSED_DATA.zip' in os.listdir(sess_path):
                            print("INFO: data already found in {} !".format(df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1]))
                        else:
                        #     print("INFO: Create PROCESSED_DATA folder in {} folder")
                        #     os.mkdir(process_dir)
                            print("Downloading all.zip")
                            with open(os.path.join(input, df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1], "all.zip"), 'wb') as f:
                                for chunk in res.iter_content(chunk_size=1024): 
                                    if chunk:
                                        f.write(chunk)
                            # file_newname = "ortho_" + df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1] + ".tif"
                            file_newname = 'PROCESSED_DATA.zip'
                            print("Renaming all.zip to PROCESSED_DATA.zip")
                            os.rename(os.path.join(sess_path, "all.zip"), os.path.join(sess_path, file_newname))
                            print("Saved " + file_newname)

                        res = requests.get(settings.SERVER + "/api/projects/{}/tasks/{}/download/report.pdf".format(project_id, task_id), 
                                            headers={'Authorization': 'JWT {}'.format(token)},
                                            stream=True)
                        pdf_newname = '000_photogrammetry_report.pdf'
                        if pdf_newname in os.listdir(sess_path):
                            print("INFO: PDF already found in {} !".format(df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1]))
                        else:
                            print("Downloading report.pdf")
                            with open(os.path.join(input, df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1], "report.pdf"), 'wb') as pdf:
                                for chunk in res.iter_content(chunk_size=1024): 
                                    if chunk:
                                        pdf.write(chunk)
                            
                            os.rename(os.path.join(sess_path, "report.pdf"), os.path.join(sess_path, pdf_newname))
                            print("Saved " + pdf_newname)                    
            ### Enrich Metadata
            dfdlodm = df
            dfdlodm.iloc[p, dfdlodm.columns.get_loc('Provenance')] = dfdlodm.iloc[p]["Provenance"] + "_\nprocess:Download from WebODM"
            dfdlodm.iloc[p, dfdlodm.columns.get_loc('Format')] = "resource:image/tiff_\ndistribution:image/tiff[GeoTIFF]"
            dfdlodm.iloc[p, dfdlodm.columns.get_loc('Data')] = pdf_newname + "@"+ os.path.join(sess_path, pdf_newname) + "," + file_newname + "@"+ os.path.join(sess_path, file_newname) + "_\nsourceType:other_\nsourceZip:False"

Successfully Logged-in!
########
id name permissions
----------
264 20231208_REU-SAINTLEU_UAV_03
263 Cap Homard
261 herbier centre nord
259 saline blanchissement ?
258 HERBIER-MNS-20240301-sud
256 Herbier-MNS-20240301-nord
255 HERBIER-MNS-20240301-centre
252 Test ortho boucan new georef
251 20231204_Ermitage
250 HERBIER-MNS-202402
248 20231208_St_Leu_Vague
245 20231208_StLeu_Zat
243 20231206_devant_Nautile
236 20231202_60m
235 20231202_40m
228 test-serge-nov2023
217 20220910_MYT-jollyroger_UAV-02_2
196 PyWebODM - 20230430_MDG-Nosy-Ve_UAV-01_3
195 PyWebODM - 20230502_MDG-Sarodrano-IOT_UAV-01_5
194 PyWebODM - 20230427_MDG-Toliara-Mangroves_UAV-01_1
193 20230430_MDG-Nosy-Ve_UAV-01_6
189 PyWebODM - 20230916_MDG-nosy-sakatia_UAV-02_1
160 PyWebODM - 20221024_SYC-aldabra-passe-arm01_UAV-02_28
159 PyWebODM - 20221021_SYC-aldabra-arm01_UAV-02_10
156 PyWebODM - 20221024_SYC-aldabra-gigi_UAV-02_31
155 PyWebODM - 20221024_SYC-aldabra-gigi_UAV-02_30
154 PyWebODM - 20221024_SYC-aldabra-gigi_UAV-02_2

In [57]:
### Reformat dataframe

for entities in range(len(df)):
    sess_path = os.path.join(
        input, df.iloc[entities]["Identifier"].split("_\n")[0].split(":")[1]
    )
    df.iloc[entities, df.columns.get_loc("Title")] = df.iloc[entities][
        "Title"
    ].replace(
        "Aerial images collected by UAV,",
        "Orthophoto & DEM from drone images, UAV,",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "This dataset was collected by an Unmanned Aerial Vehicle",
        "This dataset presents the results of the photogrammetry process using images collected by an Unmanned Aerial Vehicle",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "Underwater or aerial images collected by scientists",
        "The processing was carried out with the OpenDroneMap software from the raw images provided in the first version of this DOI.\n<br />Underwater or aerial images collected by scientists",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "<br /><b>The depot consists of the following elements:</b>",
        "<br /><br />The parameters of the OpenDroneMap software are shared so that the proposed processes can be reproduced or improved:<br />\n[\n<br />        {\n<br />            'name': 'orthophoto-resolution',\n<br />            'value': 1\n<br />        },\n<br />        {\n<br />            'name': 'auto-boundary',\n<br />            'value': true\n<br />        },\n<br />        {\n<br />            'name': 'dem-resolution',\n<br />            'value': '2.0'\n<br />        },\n<br />        {\n<br />            'name': 'dsm',\n<br />            'value': true\n<br />        }\n<br />    ]\n<br />\n<br /><b>The depot consists of the following elements:</b>",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "<br />- METADATA.zip: Exif metadata in CSV format, OGC metadata in ISO19115 / 39 XML format, flight reports with thumbnails of drone images (tb folder) and flight statistics (html or pdf files).",
        "<br />- METADATA.zip: Exif metadata in CSV format, OGC metadata in ISO19115 / 39 XML format, flight reports with thumbnails of drone images and flight statistics (html or pdf files),\n<br />- PROCESSED_DATA.zip: Orthophoto, DEM, point cloud, ...",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "<br />│--------  └─ METADATA",
        "<br />│--------  └─ METADATA\n<br />│--------  └─ PROCESSED_DATA\n<br />",
    )
#    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
#        "Description"
#    ].replace(
#        "\n<br />Les dépôts suivants comprennent les données traitées avec OpenDroneMap",
#        "",
#    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "\n<br />More recent versions of this repository are available. These include data processed with OpenDroneMap",
        "",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace("RAW DATA", "PROCESSED DATA")
    df.iloc[entities, df.columns.get_loc("Provenance")] = (
        df.iloc[entities]["Provenance"] + "_\nprocess:Download from WebODM"
    )
    df.iloc[
        entities, df.columns.get_loc("Format")
    ] = "resource:image/tiff_\ndistribution:image/tiff[GeoTIFF]"
    df.iloc[entities, df.columns.get_loc("Data")] = (
        "source:"
        + pdf_newname
        + "@"
        + os.path.join(sess_path, pdf_newname)
        + ","
        + file_newname
        + "@"
        + os.path.join(sess_path, file_newname)
        + "_\nsourceType:other"
    )


In [58]:
df.iloc[1]["Data"]

'source:000_photogrammetry_report.pdf@/home/sylvain/HDD5To/DATA/ALDABRA/20221025_SYC-aldabra-arm01_UAV-02_33/000_photogrammetry_report.pdf,PROCESSED_DATA.zip@/home/sylvain/HDD5To/DATA/ALDABRA/20221025_SYC-aldabra-arm01_UAV-02_33/PROCESSED_DATA.zip_\nsourceType:other'

In [59]:
### Export processed data df to csv
# fname = out_prefix + '_zenodo-rawdata'
# df.to_csv(os.path.join(output, fname + ".csv"), quoting=1, quotechar='"', index=False)
df.to_csv(os.path.join(output, out_prefix + "_processed_data.csv"), quoting=1, quotechar='"', index=False)

In [60]:
print(df.iloc[0]["Identifier"])
print(df.iloc[0]["Title"])
print(df.iloc[0]["Description"])
print(df.iloc[0]["Data"])

id:20221023_SYC-aldabra-arm06_UAV-02_21_
doi:10.5281/zenodo.12522502
title:Orthophoto & DEM from drone images, UAV, Aldabra arm06, Seychelles - 20221023 - 02_21
abstract:"This dataset presents the results of the photogrammetry process using images collected by an Unmanned Aerial Vehicle in Aldabra arm06, Seychelles, on 20221023
<br /> 
<br />The processing was carried out with the OpenDroneMap software from the raw images provided in the first version of this DOI.
<br />Underwater or aerial images collected by scientists or citizens can have a wide variety of uses for science, ecosystems management, or conservation. These images can be annotated and shared to train IA models which can in turn predict the objects on such images. We provide a set of tools (hardware and software) to collect marine data, predict species or habitat, and provide maps.
<br />
<br /><br />The parameters of the OpenDroneMap software are shared so that the proposed processes can be reproduced or improved:<br />


In [61]:
### UNZIP PROCESSED_DATA
from zip_helper import *
for entities in range(len(df)):
    print("unzip PROCESSED_DATA.zip in: ", sess_path)
    sess_path = os.path.join(
        input, df.iloc[entities]["Identifier"].split("_\n")[0].split(":")[1]
    )
    try:
        unzip(sess_path, 'PROCESSED_DATA.zip', 'PROCESSED_DATA/PHOTOGRAMMETRY/')
    except:
        print("no_zip in: ", sess_path)
    print("Remove zip")
    try:
        os.remove(os.path.join(sess_path, 'PROCESSED_DATA.zip'))
    except:
        print("no_zip to remove in: ", sess_path)
        
    print("Recreate zip")
    zip_folder(os.path.join(sess_path, 'PROCESSED_DATA'), os.path.join(sess_path, 'PROCESSED_DATA'))
    

unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_17
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/ALDABRA/20221023_SYC-aldabra-arm06_UAV-02_21
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/ALDABRA/20221025_SYC-aldabra-arm01_UAV-02_33
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/ALDABRA/20221022_SYC-aldabra-passe-dubois_UAV-02_14
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/ALDABRA/20221024_SYC-aldabra-passe-dubois-MSP_UAV-02_27
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/ALDABRA/20221020_SYC-aldabra-arm01_UAV-02_3
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/ALDABRA/20221020_SYC-aldabra-arm01_UAV-02_6
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/ALDABRA/20221024_SYC-aldabra-passe-dubois-40m_UAV-02_

### Geoflow to upload processed data

In [73]:
# ### Execute geoflow :: upload to geoflow
# # config_raw = os.path.join(output, out_prefix + '_rawfiles-config.json')
# pdata = os.path.join(output, 'comores_processed.json')
# # run_geoflow(config_raw, geoflow_folder)
# os.chdir(geoflow_folder)
# # subprocess.run(["R", "-e", "geoflow::initWorkflow('{}')".format(config_raw)], capture_output=False)
# subprocess.call(["R", "-e", "geoflow::executeWorkflow('{}')".format(pdata)],
#                 stdout=subprocess.DEVNULL, stderr=subprocess.STDOUT,)
# os.chdir(dronemdt_folder)

### Upload processed data with python

In [63]:
### Upload processed_data to Zenodo
print("#### Upload zip files to Zenodo")
base_url = "https://zenodo.org/api/"
for zipul in range(len(df)):
    print('\nDataset:', zipul+1, "/" ,len(df), "\n    ",df.iloc[zipul]['Identifier'])
    zenodo_baseurl = base_url
    
    #### Extract source from Data in dataframe
    data_zip = df.iloc[zipul]['Data'].split('source:')[1].split('_\n')[0]
    if "," in data_zip:
        data_ziptemp = data_zip.split(',')
        data_zip = []
        for dt in range(len(data_ziptemp)):
            data_zip.append(data_ziptemp[dt].split('@')[0])
    else:
        data_zip = data_zip.split('@')[0]
    # data_zip = source_file
    print(data_zip)
    
    
    if 'doi:' in df.iloc[zipul]['Identifier']:
        doi_raw = df.iloc[zipul]['Identifier'].split('_\ndoi:')[1].split('\n')[0].split('.')[-1]
        print("DOI already present: ",doi_raw)
        getrecid = zenlist_single(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
        
        if int(doi_raw) == int(getrecid.json()['conceptdoi'].split('.')[-1]) + 1 :
            print("New deposit version")
            newv = zen_newversion(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
            zenval = zenvar(newv)
            print("New doi version:"+zenval[1])

            print("Write DOI to dataframe")
            df.iloc[zipul, df.columns.get_loc('Identifier')] = "id:" + df.iloc[zipul]['Identifier'].split('_\n')[0].split('id:')[1] + "_\ndoi:" + zenval[1]
            
            print("Enrich upload with metadata")
            df.iloc[zipul, df.columns.get_loc("Provenance")] = df.iloc[zipul]["Provenance"] + "_\nprocess:Processed data uploaded to " + base_url.split('api')[0] + "record/" + str(zenval[2])
        
        else:
            print('Version in draft status')
            zenval = zenvar(getrecid)
        
        print("Enrich upload with metadata")
        zen_metadata = zenmdt(zenodo_baseurl, ACCESS_TOKEN, zenval[2], df, zipul)
        
    else:
        print("Initialize deposit")
        r = check_token(zenodo_baseurl, ACCESS_TOKEN)
        zenval = zenvar(r)
        print("prereserved doi:"+zenval[1])
        print("Write DOI to dataframe")
        dfzen = df
        if 'doi:' in dfzen.iloc[zipul]['Identifier']:
            pass
        else:
            dfzen.iloc[zipul, dfzen.columns.get_loc('Identifier')] = "id:" + dfzen.iloc[zipul]['Identifier'] + "_\ndoi:" + zenval[1]
            dfzen.iloc[zipul, dfzen.columns.get_loc("Provenance")] = dfzen.iloc[zipul]["Provenance"] + "_\nprocess:Processed dataset uploaded to " + base_url.split('api')[0] + "record/" + str(zenval[2])
            
        print("Enrich upload with metadata")
        zen_metadata = zenmdt(zenodo_baseurl, ACCESS_TOKEN, zenval[2], df, zipul)
        if zen_metadata.status_code > 400:
            print("error in metadata, please check there is no double keywords: \n" + zen_metadata.text)
            break 

    print("upload data")
    print("    Trying upload number: 1")
    
    for file in data_zip:
        ul_count = 1
        ### Control Filename
        # while file not in zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2])).text:
        ### Control md5 checksum:
        ful = os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1], file)
        print(ful)
        with open(ful, "rb") as file_to_check:
            # Open,close, read file and calculate MD5 on its contents 
            # read contents of the file
            ## Python 3.10
            fh = file_to_check.read() 
            # pipe contents of the file through
            digest = hashlib.md5(fh)
            ## End Python 3.10
            # digest = hashlib.file_digest(file_to_check, "md5") ### Python 3.11 only
        print("    md5:", digest.hexdigest())
        while digest.hexdigest() not in zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2])).text:
            #Reset connection every 15 tries
            if ul_count == 15:
                getrecid = zenlist_single(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
                zenval = zenvar(getrecid)
            
            file_on_server = zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2]))
            ### Clean wrong checksum
            if file in file_on_server.text:
                print("    clean wrong files")
                for fs in range(len(file_on_server.json())):
                    if file == file_on_server.json()[fs]['filename']:
                        # print("    sleep 5: computing checksum on server")
                        # time.sleep(15)
                        print("    checksum on server", file_on_server.json()[fs]['checksum'])
                        furl = file_on_server.json()[fs]["links"]["self"]
                        file_to_remove = zen_del_file(furl, ACCESS_TOKEN)
                        
            file_list = [file]            
            zen_upload = zenul(zenval[0], ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), file_list)
            print("        ", zen_upload.text)
            if zen_upload.status_code == 404:
                print("Version doesn't exists ! Please check your record_id")
                break
            else:
                ul_count += 1
                print("    Retry number: " + str(ul_count))
                if zen_upload.status_code == 403:
                    print("        Friday 13th 2023 nightmare => permission denied!")
                    time.sleep(5)    

    ### Publish to Zenodo
    # print("Publish record")
    # published = zenpublish(zenodo_baseurl, ACCESS_TOKEN, zenval[2])
    # print(published.text)

#### Upload zip files to Zenodo

Dataset: 1 / 33 
     id:20221023_SYC-aldabra-arm06_UAV-02_21_
doi:10.5281/zenodo.12522502
['000_photogrammetry_report.pdf', 'PROCESSED_DATA.zip']
DOI already present:  12522502
New deposit version
New doi version:10.5281/zenodo.12528494
Write DOI to dataframe
Enrich upload with metadata
Enrich upload with metadata
No contact file, email will be displayed in Zenodo !
{'metadata': {'title': 'Orthophoto & DEM from drone images, UAV, Aldabra arm06, Seychelles - 20221023 - 02_21', 'publication_date': '2024-06-24', 'description': '"This dataset presents the results of the photogrammetry process using images collected by an Unmanned Aerial Vehicle in Aldabra arm06, Seychelles, on 20221023\n<br /> \n<br />The processing was carried out with the OpenDroneMap software from the raw images provided in the first version of this DOI.\n<br />Underwater or aerial images collected by scientists or citizens can have a wide variety of uses for science, ecosystems managem

In [64]:
### Check DOI's

for doi in range(len(df)):
    print(df.iloc[doi]["Identifier"])

id:20221023_SYC-aldabra-arm06_UAV-02_21_
doi:10.5281/zenodo.12528494
id:20221025_SYC-aldabra-arm01_UAV-02_33_
doi:10.5281/zenodo.12528499
id:20221022_SYC-aldabra-passe-dubois_UAV-02_14_
doi:10.5281/zenodo.12528513
id:20221024_SYC-aldabra-passe-dubois-MSP_UAV-02_27_
doi:10.5281/zenodo.12528521
id:20221020_SYC-aldabra-arm01_UAV-02_3_
doi:10.5281/zenodo.12528536
id:20221020_SYC-aldabra-arm01_UAV-02_6_
doi:10.5281/zenodo.12528543
id:20221024_SYC-aldabra-passe-dubois-40m_UAV-02_26_
doi:10.5281/zenodo.12528558
id:20221020_SYC-aldabra-arm01_UAV-02_4_
doi:10.5281/zenodo.12528585
id:20221023_SYC-aldabra-arm06_UAV-02_20_
doi:10.5281/zenodo.12528596
id:20221020_SYC-aldabra-arm01_UAV-02_5_
doi:10.5281/zenodo.12528615
id:20221021_SYC-aldabra-arm01_UAV-02_8_
doi:10.5281/zenodo.12528621
id:20221022_SYC-aldabra-arm06_UAV-02_16_
doi:10.5281/zenodo.12528633
id:20221024_SYC-aldabra-gigi_UAV-02_30_
doi:10.5281/zenodo.12528637
id:20221019_SYC-aldabra-arm01_UAV-02_1_
doi:10.5281/zenodo.12528670
id:20221023_

In [65]:
### Export processed data df to csv
# fname = out_prefix + '_zenodo-rawdata'
# df.to_csv(os.path.join(output, fname + ".csv"), quoting=1, quotechar='"', index=False)
df.to_csv(os.path.join(output, out_prefix + "_processed_data_updated_doi.csv"), quoting=1, quotechar='"', index=False)
# # config_raw = os.path.join(output, out_prefix + '_rawfiles-config.json')


In [66]:
### Update Metadata
print("#### Update metadata")
base_url = "https://zenodo.org/api/"
for zipul in range(len(df)):
    print('\nDataset:', zipul+1, "/" ,len(df), "\n    ",df.iloc[zipul]['Identifier'])
    zenodo_baseurl = base_url 
    
    if 'doi:' in df.iloc[zipul]['Identifier']:
        doi_raw = df.iloc[zipul]['Identifier'].split('_\ndoi:')[1].split('_\n')[0].split('.')[-1]
        # print("\nDOI already present: ",doi_raw)
        # getrecid = zenlist_single(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
        # print(getrecid.text)
        
        # zenval = zenvar(getrecid)
        # print(zenval)
        # print("\nEnrich upload with metadata")
        zenedit(zenodo_baseurl, ACCESS_TOKEN, doi_raw)
        zen_metadata = zenmdt(zenodo_baseurl, ACCESS_TOKEN, doi_raw, df, zipul, contact_file="/home/sylvain/DroneMDT/geoflow_g2oi_contacts.csv")
        print(zen_metadata)

    ### Publish to Zenodo
    print("Publish record")
    published = zenpublish(zenodo_baseurl, ACCESS_TOKEN, doi_raw)
    print(published.text)

#### Update metadata

Dataset: 1 / 33 
     id:20221023_SYC-aldabra-arm06_UAV-02_21_
doi:10.5281/zenodo.12528494
Using contact file
  Looking for julien.barde@ird.fr
    Look for email julien.barde@ird.fr in Contact file
      Add orcid
      Add First and Last Name
      Add Affiliation
  Looking for sylvain.bonhommeau@ifremer.fr
    Look for email sylvain.bonhommeau@ifremer.fr in Contact file
      Add orcid
      Add First and Last Name
      Add Affiliation
  Looking for victor.illien@ifremer.fr
    Look for email victor.illien@ifremer.fr in Contact file
      Add First and Last Name
      Add Affiliation
  Looking for matteo.contini@ifremer.fr
    Look for email matteo.contini@ifremer.fr in Contact file
      Add orcid
      Add First and Last Name
      Add Affiliation
  Looking for serge.bernard@lirmm.fr
    Look for email serge.bernard@lirmm.fr in Contact file
      Add First and Last Name
      Add Affiliation
  Looking for sylvain.poulain@ird.fr
    Look for email sylvain.pou